# Ideas

## How do video Games Age? 
Graph showing the development of Metrics over time (group by, TOP 10, Genre, Main Publishers..)

Motivation:  
* Some games are incredibly well reviewd when they come out, but eventually tend to age poorly. (Simply Analysis but we can also measure the NLP)
* Monitoring of Discourse overtime

Code Steps:
* Apply Regression, get the inclination of the curve and sort (both by the positive and negative) by that (we'll see the stipest inclination)


## Plataform level aanalysis

* Sentiment overtime of the main plataforms

# EDA & Data Loading

___
## Games Summary


In [2]:
# Import libraries
import pandas as pd
import numpy as np
import project_data_utils

# NLP libraries
from textblob import TextBlob
from textblob import Word
import spacy_fastlang
import spacy
import nltk


# Data vizualization Libraries
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot 
init_notebook_mode(connected=True)
import cufflinks as cf
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

In [2]:
# Load df_games
df_games = pd.read_csv("data/metacritic_games_full.csv" ,index_col=0)
df_games['user_score'] = pd.to_numeric(df_games['user_score'],errors='coerce')
df_games['metacritic_user_differenc'] = df_games['metascore'] - df_games['user_score']
# Create metascore and user discrepancy and tranform to numeric
df_games.sort_values(by='metacritic_user_differenc')
df_games.head(5)

title       platform  release_date  \
0              Persona 5 Royal             pc  Oct 21, 2022   
1                   Elden Ring  xbox-series-x  Feb 25, 2022   
2                   Elden Ring  playstation-5  Feb 25, 2022   
3  Portal Companion Collection         switch  Jun 28, 2022   
4              Persona 5 Royal  xbox-series-x  Oct 21, 2022   

                                     other_platforms  metascore  user_score  \
0  ['PlayStation 4', 'PlayStation 5', 'Switch', '...       97.0         8.9   
1  ['PC', 'PlayStation 4', 'PlayStation 5', 'Xbox...       96.0         7.7   
2  ['PC', 'PlayStation 4', 'Xbox One', 'Xbox Seri...       96.0         7.9   
3                                                NaN       96.0         8.3   
4  ['PC', 'PlayStation 4', 'PlayStation 5', 'Swit...       95.0         8.4   

        developer           publisher  \
0           Atlus                Sega   
1   From Software  Bandai Namco Games   
2   From Software  Bandai Namco Games   
3  Valve Software      Valve Software   
4           Atlus                Sega   

                                               genre                players  \
0  ['Role-Playing', ',                           ...  No Online Multiplayer   
1  ['Role-Playing', ',                           ...               Up to 4    
2  ['Role-Playing', ',                           ...               Up to 4    
3  ['Miscellaneous', ',                          ...                    NaN   
4  ['Role-Playing', ',                           ...  No Online Multiplayer   

  rating                                            summary  \
0    NaN  Prepare for an all-new RPG experience in Perso...   
1      M  A New World Created By Hidetaka Miyazaki And G...   
2      M  A New World Created By Hidetaka Miyazaki And G...   
3    NaN  Including Portal and Portal 2, the Companion C...   
4      M  Prepare for an all-new RPG experience in Perso...   

                                                 url  \
0     https://metacritic.com/game/pc/persona-5-royal   
1  https://metacritic.com/game/xbox-series-x/elde...   
2  https://metacritic.com/game/playstation-5/elde...   
3  https://metacritic.com/game/switch/portal-comp...   
4  https://metacritic.com/game/xbox-series-x/pers...   

   metacritic_user_differenc  
0                       88.1  
1                       88.3  
2                       88.1  
3                       87.7  
4                       86.6

In [3]:
# Check dtypes
df_games.dtypes

title                         object
platform                      object
release_date                  object
other_platforms               object
metascore                    float64
user_score                   float64
developer                     object
publisher                     object
genre                         object
players                       object
rating                        object
summary                       object
url                           object
metacritic_user_differenc    float64
dtype: object

## User Reviews

In [21]:
df_user_rev = pd.read_csv("data/metacritic_user_reviews_full.csv")
df_user_rev_full = df_user_rev # full copy
df_user_rev.head()

Unnamed: 0                                             url  \
0           0  https://metacritic.com/game/pc/persona-5-royal   
1           1  https://metacritic.com/game/pc/persona-5-royal   
2           2  https://metacritic.com/game/pc/persona-5-royal   
3           3  https://metacritic.com/game/pc/persona-5-royal   
4           4  https://metacritic.com/game/pc/persona-5-royal   

             title platform  user_score        reviewer  \
0  Persona 5 Royal       pc          10         Trix122   
1  Persona 5 Royal       pc           7          Runwin   
2  Persona 5 Royal       pc          10       Godskrieg   
3  Persona 5 Royal       pc          10    jackspade152   
4  Persona 5 Royal       pc          10  MLGANDREWPLAYS   

                                              review          date  \
0  \n100+ h of main story , good gameplay and pro...  Oct 25, 2022   
1  El juego tiene una cantidad de relleno abrumad...  Oct 26, 2022   
2  \nAbsolute god of recent JRPGs.\rIf you like t...  Oct 24, 2022   
3  \nSimply amazing. I finished this Game on ps4 ...  Oct 25, 2022   
4  People have been waiting for a long time for t...  Oct 25, 2022   

  review_type                                           url_page  
0        user  https://metacritic.com/game/pc/persona-5-royal...  
1        user  https://metacritic.com/game/pc/persona-5-royal...  
2        user  https://metacritic.com/game/pc/persona-5-royal...  
3        user  https://metacritic.com/game/pc/persona-5-royal...  
4        user  https://metacritic.com/game/pc/persona-5-royal...

### Group by Title

In [5]:
# Group by title so we remove the platform granularity
df_user_rev.groupby(['title']).size().sort_values()

df_user_rev = df_user_rev.groupby(['title']).agg({'url':'count', 'user_score':'mean', 'reviewer':'count'}).sort_values(by='url')
df_user_rev = df_user_rev.rename(columns={'url':'num_user_reviews', 'user_score': 'avg_user_score', 'reviewer':'num_user_reviewers'})
df_user_rev.sort_values(by='num_user_reviews', ascending=False)

num_user_reviews  avg_user_score  \
title                                                              
Cyberpunk 2077                             12058        5.056394   
Warcraft III: Reforged                     10100        0.070198   
The Last of Us Part II                     10100        4.112376   
Ghost of Tsushima                           9505        9.289637   
Death Stranding                             8764        7.219763   
...                                          ...             ...   
Trulon: The Shadow Engine                      1        6.000000   
Tumblestone                                    1        0.000000   
Fallen Legion: Revenants                       1        9.000000   
Oblitus                                        1        4.000000   
void tRrLM(); //Void Terrarium                 1       10.000000   

                                num_user_reviewers  
title                                               
Cyberpunk 2077                               12058  
Warcraft III: Reforged                       10100  
The Last of Us Part II                       10100  
Ghost of Tsushima                             9505  
Death Stranding                               8764  
...                                            ...  
Trulon: The Shadow Engine                        1  
Tumblestone                                      1  
Fallen Legion: Revenants                         1  
Oblitus                                          1  
void tRrLM(); //Void Terrarium                   1  

[6438 rows x 3 columns]

## Critic Reviews

### Title Aggregated Data

In [22]:
df_critic_rev = pd.read_csv("data/metacritic_critic_reviews_full.csv")
df_critic_rev_full = df_critic_rev #full copy
df_critic_rev.head()

Unnamed: 0                                             url  \
0           0  https://metacritic.com/game/pc/persona-5-royal   
1           1  https://metacritic.com/game/pc/persona-5-royal   
2           2  https://metacritic.com/game/pc/persona-5-royal   
3           3  https://metacritic.com/game/pc/persona-5-royal   
4           4  https://metacritic.com/game/pc/persona-5-royal   

             title platform  user_score          reviewer  \
0  Persona 5 Royal       pc          99         Game Rant   
1  Persona 5 Royal       pc          97     God is a Geek   
2  Persona 5 Royal       pc          95  The Mako Reactor   
3  Persona 5 Royal       pc          95     Hooked Gamers   
4  Persona 5 Royal       pc          94    Hobby Consolas   

                                              review          date  \
0  From its captivating music and memorable story...  Oct 17, 2022   
1  Persona 5 Royal is quite frankly one of the be...  Oct 17, 2022   
2  Persona 5 Royal was already the best version o...  Oct 17, 2022   
3  Persona 5 Royal is chock full of amazing music...  Oct 28, 2022   
4  If you love RPGs and didn't play it on PS4, do...  Oct 17, 2022   

  review_type                                           url_page  
0      critic  https://metacritic.com/game/pc/persona-5-royal...  
1      critic  https://metacritic.com/game/pc/persona-5-royal...  
2      critic  https://metacritic.com/game/pc/persona-5-royal...  
3      critic  https://metacritic.com/game/pc/persona-5-royal...  
4      critic  https://metacritic.com/game/pc/persona-5-royal...

In [7]:
df_critic_rev.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 433384 entries, 0 to 433383
Data columns (total 10 columns):
 #   Column       Non-Null Count   Dtype 
---  ------       --------------   ----- 
 0   Unnamed: 0   433384 non-null  int64 
 1   url          433384 non-null  object
 2   title        433384 non-null  object
 3   platform     433384 non-null  object
 4   user_score   433384 non-null  int64 
 5   reviewer     433384 non-null  object
 6   review       433362 non-null  object
 7   date         244119 non-null  object
 8   review_type  433384 non-null  object
 9   url_page     433384 non-null  object
dtypes: int64(2), object(8)
memory usage: 33.1+ MB


In [8]:
# Group by title so we remove the platform granularity
df_critic_rev.groupby(['title']).size().sort_values()

df_critic_rev = df_critic_rev.groupby(['title']).agg({'url':'count', 'user_score':'mean', 'reviewer':'count'}).sort_values(by='url')
df_critic_rev = df_critic_rev.rename(columns={'url':'num_critic_reviews', 'user_score': 'avg_critic_score', 'reviewer':'num_critic_reviewers'})

In [9]:
df_critic_rev

num_critic_reviews  avg_critic_score  \
title                                                             
EyePet: Move Edition                        1         91.000000   
Kingdom Hearts 358/2 Days                   1         90.000000   
BioShock 2: Minerva's Den                   1         91.000000   
DCS: Black Shark                            1         94.000000   
Tournament of Legends                       1         80.000000   
...                                       ...               ...   
Madden NFL 07                             224         80.156250   
X-Men: The Official Game                  224         52.843750   
Marvel: Ultimate Alliance                 229         80.371179   
Resident Evil 5                           231         81.155844   
Spider-Man 2                              249         74.678715   

                           num_critic_reviewers  
title                                            
EyePet: Move Edition                          1  
Kingdom Hearts 358/2 Days                     1  
BioShock 2: Minerva's Den                     1  
DCS: Black Shark                              1  
Tournament of Legends                         1  
...                                         ...  
Madden NFL 07                               224  
X-Men: The Official Game                    224  
Marvel: Ultimate Alliance                   229  
Resident Evil 5                             231  
Spider-Man 2                                249  

[12654 rows x 3 columns]

## Join Games with User and Critic Reviews


In [10]:
# join on user_rev
df = df_games.merge(df_user_rev, on='title', how='left', indicator=True)
df = df.rename(columns={'_merge': 'merge_indicator_user_revs'})

In [11]:
# join on critic_rev
df = df.merge(df_critic_rev, on='title', how='left', indicator=True)
df = df.rename(columns={'_merge': 'merge_indicator_critic_revs'})
df

title       platform  release_date  \
0                    Persona 5 Royal             pc  Oct 21, 2022   
1                         Elden Ring  xbox-series-x  Feb 25, 2022   
2                         Elden Ring  playstation-5  Feb 25, 2022   
3        Portal Companion Collection         switch  Jun 28, 2022   
4                    Persona 5 Royal  xbox-series-x  Oct 21, 2022   
...                              ...            ...           ...   
19634        Resident Evil: Survivor    playstation  Aug 30, 2000   
19635               ECW Anarchy Rulz      dreamcast  Dec 30, 2000   
19636  Duke Nukem: Land of the Babes    playstation  Sep 19, 2000   
19637  Mortal Kombat: Special Forces    playstation  Jun 30, 2000   
19638                     HBO Boxing    playstation  Nov 20, 2000   

                                         other_platforms  metascore  \
0      ['PlayStation 4', 'PlayStation 5', 'Switch', '...       97.0   
1      ['PC', 'PlayStation 4', 'PlayStation 5', 'Xbox...       96.0   
2      ['PC', 'PlayStation 4', 'Xbox One', 'Xbox Seri...       96.0   
3                                                    NaN       96.0   
4      ['PC', 'PlayStation 4', 'PlayStation 5', 'Swit...       95.0   
...                                                  ...        ...   
19634                                                NaN       39.0   
19635                                                NaN       38.0   
19636                                                NaN       37.0   
19637                                                NaN       28.0   
19638                                                NaN       26.0   

       user_score                       developer           publisher  \
0             8.9                           Atlus                Sega   
1             7.7                   From Software  Bandai Namco Games   
2             7.9                   From Software  Bandai Namco Games   
3             8.3                  Valve Software      Valve Software   
4             8.4                           Atlus                Sega   
...           ...                             ...                 ...   
19634         6.2                          Capcom              Capcom   
19635         6.8  Acclaim Studios Salt Lake City             Acclaim   
19636         6.9                         n-Space      GT Interactive   
19637         2.8                          Midway              Midway   
19638         4.0                  Osiris Studios             Acclaim   

                                                   genre  \
0      ['Role-Playing', ',                           ...   
1      ['Role-Playing', ',                           ...   
2      ['Role-Playing', ',                           ...   
3      ['Miscellaneous', ',                          ...   
4      ['Role-Playing', ',                           ...   
...                                                  ...   
19634  ['Action Adventure', ',                       ...   
19635  ['Action', ',                                 ...   
19636  ['Action', ',                                 ...   
19637  ['Action', ',                                 ...   
19638  ['Sports', ',                                 ...   

                     players  ...  \
0      No Online Multiplayer  ...   
1                   Up to 4   ...   
2                   Up to 4   ...   
3                        NaN  ...   
4      No Online Multiplayer  ...   
...                      ...  ...   
19634               1 Player  ...   
19635                    NaN  ...   
19636                   1-2   ...   
19637               1 Player  ...   
19638                    NaN  ...   

                                                     url  \
0         https://metacritic.com/game/pc/persona-5-royal   
1      https://metacritic.com/game/xbox-series-x/elde...   
2      https://metacritic.com/game/playstation-5/elde...   
3      https://metacritic.com/game/switch/portal-comp...   
4     

## Define Working Data Frame

In [12]:
print('before droppping rows with null reviews: ', df.shape)
print('after droppping rows with null reviews: ', df.dropna(subset=['num_user_reviews']).shape)
# drop null

df = df.dropna(subset=['num_user_reviews'])
df.shape

before droppping rows with null reviews:  (19639, 22)
after droppping rows with null reviews:  (10751, 22)


(10751, 22)

In [20]:
# Get only one platform.
# !Change to include averages
df = df.groupby('title').first()
df = df.sort_values(by='num_user_reviews', ascending=False).head(100)

In [33]:
# Get the top N games and pass to a list
lst_games = df.index.tolist()
len(lst_games)

100

# NLP

## NLP Pre-process

### Select Workig dataframe for NLP task

In [48]:
# Select only a subset of the reviews
df_user_rev = df_user_rev_full[df_user_rev_full['title'].isin(lst_games)]
print('Number of reviews: ' ,df_user_rev.shape)

Number of reviews:  (312082, 10)


In [53]:
df_user_rev

Unnamed: 0                                                url  \
31              31  https://metacritic.com/game/xbox-series-x/elde...   
32              32  https://metacritic.com/game/xbox-series-x/elde...   
33              33  https://metacritic.com/game/xbox-series-x/elde...   
34              34  https://metacritic.com/game/xbox-series-x/elde...   
35              35  https://metacritic.com/game/xbox-series-x/elde...   
...            ...                                                ...   
723835      723835  https://metacritic.com/game/wii/call-of-duty-m...   
723836      723836  https://metacritic.com/game/wii/call-of-duty-m...   
723837      723837  https://metacritic.com/game/wii/call-of-duty-m...   
723838      723838  https://metacritic.com/game/wii/call-of-duty-m...   
723839      723839  https://metacritic.com/game/wii/call-of-duty-m...   

                                 title       platform  user_score  \
31                          Elden Ring  xbox-series-x          10   
32                          Elden Ring  xbox-series-x           7   
33                          Elden Ring  xbox-series-x           3   
34                          Elden Ring  xbox-series-x           0   
35                          Elden Ring  xbox-series-x          10   
...                                ...            ...         ...   
723835  Call of Duty: Modern Warfare 3            wii          10   
723836  Call of Duty: Modern Warfare 3            wii          10   
723837  Call of Duty: Modern Warfare 3            wii           8   
723838  Call of Duty: Modern Warfare 3            wii          10   
723839  Call of Duty: Modern Warfare 3            wii           0   

              reviewer                                             review  \
31          Sekiro1990  The best game from FROM SOFTWARE so farSome fr...   
32          Netherghul  Not a terrible game. But failing of expectatio...   
33      MingledLotus24  I dont like it too much. Neither aesthetics, n...   
34            SlavisaT  the game is big garbage, the world is empty, g...   
35             Jakob44  The game is good, no microtransactions and a f...   
...                ...                                                ...   
723835     Wesleytorna  Call of duty modern warfare 3 on the wii is a ...   
723836    broken_glass  bought this game at gamestop for cheap used an...   
723837   PotatoAim1805  This version of the game is very underrated an...   
723838      AidasKar15  I love campaign and multiplayer with friends a...   
723839      kozachenko  this is an absolute rubbish console port for t...   

                date review_type  \
31      Feb 27, 2022        user   
32      Mar  6, 2022        user   
33      Apr  3, 2022        user   
34      Feb 28, 2022        user   
35      Apr 10, 2022        user   
...              ...         ...   
723835  Jan 18, 2020        user   
723836  Apr 19, 2020        user   
723837  Jun 23, 2020        user   
723838  Oct 21, 2020        user   
723839  Sep 30, 2022        user   

                                                 url_page  
31      https://metacritic.com/game/xbox-series-x/elde...  
32      https://metacritic.com/game/xbox-series-x/elde...  
33      https://metacritic.com/game/xbox-series-x/elde...  
34      https://metacritic.com/game/xbox-series-x/elde...  
35      https://metacritic.com/game/xbox-series-x/elde...  
...                                                   ...  
723835  https://metacritic.com/game/wii/call-of-duty-m...  
723836  https://metacritic.com/game/wii/call-of-duty-m...  
723837  https://metacritic.com/game/wii/call-of-duty-m...  
723838  https://metacritic.com/game/wii/call-of-duty-m...  
723839  https://metacritic.com/game/wii/call-of-duty-m...  

[312082 rows x 10 columns]

### Clean Text

In [51]:
# Function to clean the text
def preprocess(text):
    text = text.replace('\n', "")
    text = text.replace('\r', "")
    return text

In [52]:
df_user_rev['review'] = df_user_rev['review'].apply(lambda x: preprocess(x))

In [58]:
print('5 random review \n')
cl = df_user_rev.sample(5)['review'].values
for c in cl:
    print(c)

5 random review 

Really great game, especially the AI. The AI is really good. Like when you put down a tripwire robots actually jump over them! They are so smart. 10/10 would play again.
The same game.. but actually worse, don’t give them your hard earned money.
-ALERTA DE SPOILERS-Desde la propuesta inicial de una invasión mongola en la isla de Tsushima la cual provocaría la muerte de todos los samuráis existentes en la isla, salvo un par. Una propuesta cautivadora que no me hizo querer despegarme del control por muchas horas.Me encuentro en el tercer acto y con 61 horas puedo dar una opinión y de la historia, la historia empieza fuerte después decae un pelín pero se recupera y se supera brutalmente en el acto 2, en especial en la misión de la invasión al castillo Shimura y defendiendo a Yarikawa, esas dos misiones tuvieron momentos que me dejaron pasmado.... cuando masacro al líder mongol en Yarikawa, simplemente impactante. No solo por lo grafico si no por el peso narrativo. Y en e

### Detect and Remove non Enlgish Reviews

Samping the data we noticed that the dataset contained reviews in multiple languagues. In this section, we'll investitage this.

In [67]:
nlp = spacy.load("en_core_web_sm")
nlp.add_pipe("language_detector")
def detectLanguage(text):
    text = ' '.join(text.split()[:5]) # In order to save memory, analyse only the first 5 workds
    doc = nlp(text)
    return doc._.language

# print(detectLanguage("I am happy"))

In [ ]:
# Create languae_review colum
print(f'Number of rows before removing non engligh words: {df_user_rev.shape[0]} \n')
df_user_rev['language_review'] = df_user_rev['review'].map(lambda text: detectLanguage(text))

# select languages with only English Reviews
df_user_rev = df_user_rev[[df_user_rev['language_review'] == 'en']]

### Spelling Correction

### Word inflection (lemmatization) 

In [6]:
#nltk.download('wordnet')
nltk.download('omw-1.4')

[nltk_data] Downloading package omw-1.4 to /Users/gio/nltk_data...


True

In [16]:
w = Word("straightforward")
w.lemmatize()

'straightforward'

### Blob Polarity Analys

In [14]:
def getSubjectivity(text):
    return TextBlob(text).sentiment.subjectivity

#Create a function to get the polarity
def getPolarity(text):
    return TextBlob(text).sentiment.polarity

In [15]:
df_user_rev['polarity'] = df_user_rev['review'].map(lambda text: TextBlob(text).sentiment.polarity)

Positive Reviews

In [16]:
print('5 random reviews with the highest positive sentiment polarity: \n')
cl = df_user_rev.loc[df_user_rev.polarity == 1, ['review']].sample(5).values
for c in cl:
    print(c[0])

5 random reviews with the highest positive sentiment polarity: 

Ich mache mal mit bei dem Boykott, auch wenn ich es nie angespielt habe. :D
Orta dereceli bir hikaye ama muazzam bir villian ve karakter anlatımı.ve oyundaki atmosferde fena değil :D
One of the best games I ever playedOn the downside, unrealistical image of blacks at that point of time
Best sony exclusive this yearGameplay 10/10Story 10/10Graphics 10/10Sounds track 10/10Game of the year
It's very nice! Отличное дополнение! Считаю его лучшим из всех последних дополнений!


Neutral Reviews

In [17]:
print('5 random neutral reviews: \n')
cl = df_user_rev.loc[df_user_rev.polarity == 0, ['review']].sample(5).values
for c in cl:
    print(c[0])

5 random neutral reviews: 

Поиграл на приставке у друга прежде чем покупать. Рад что не купил, цена сильно высокая для такого г...
Посредственная игра с предсказуемым и скучным сюжетом не стоит своих 60$!EA попытались сделать сюжетную игру, но как обычyо бывает такие компании как EA пытаются попасть в сроки и выходит полная ерунда. Фанатам истории звездных войн не понравиться 3/10
Ужасная игра. Ждал выхода с самого анонса, так как обожал в свое время это игрушку. В 4к игра ужасно тормозила, была первая игра которую не вытянул мой ПК. Спустил разрешение до 1080 стало более менее и тогда я уже разочаровался в самом качестве перезапуска. Не покупайте.
Me hacen gracia las notas bajas intentando desprestigiar a Nintendo. Yo soy usuario de ps también pero cuando un juego es una obra maestra se dice y punto.
Grandi di gametime, mettevi a 90 e leccategli il culo ridicoli fanboy del cazzo, la professionalità l'avete persa nell'hype del vostro gioco preferito e ovviamente chi non ha la vostra o

Negative Reviews

In [18]:
print('5 random negative reviews: \n')
cl = df_user_rev.loc[df_user_rev.polarity == -1, ['review']].sample(5).values
for c in cl:
    print(c[0])

5 random negative reviews: 

Por donde comenzar es muy malo en historia y eso es algo fundamental de un juego de este estilo solo digo que al principio muere el protagonista (Joel) :'(
Boring    m
Ctrl-C ......Ctrl-V viernes 13 por este pedaso de basura resident evil se redujo
Я прошел «The Evil Within 2» и это было классно. Я давно не получал такого удовольствия, хоть и не сверх яркого. Даже как-то жаль, что продолжительное время оставлял игру на потом и только сейчас умудрился её вытащить из бэклога. Весьма трогательная и красивая история с приятным дизайном говорящих персонажей. Но не скажу, что именно сюжет оказался для меня главным блюдом. Хотя вот постановка многих моментов тут просто потрясающая. Например, погружение в прошлое или путешествие между терминала сети. Но по большей мере Я остался доволен именно игровым процессом. Прогулки на корточках по кустам в здешних полуоткрытых локациях провинциального городка в поисках припасов и забав на свою пятую точку, с уклоном на незаме

Distribution of Polarity Score

In [19]:
#The distribution of review sentiment polarity score

df_user_rev['polarity'].iplot(
    kind='hist',
    bins=50,
    xTitle='polarity',
    linecolor='black',
    yTitle='count',
    title='Sentiment Polarity Distribution')

### Distribution of Review Ratings

In [20]:
df_user_rev['user_score'].iplot(
    kind='hist',
    xTitle='rating',
    linecolor='black',
    yTitle='count',
    title='Review Rating Distribution')

### [TODO] Blob Subjectivity Analysis
Subjectivity quantifies the amount of personal opinion and factual information contained in the text. The higher subjectivity means that the text contains personal opinion rather than factual information

## N-Grams Distribution

In [22]:
from sklearn.feature_extraction.text import CountVectorizer

### 1-Gram Analysis

In [23]:
def get_top_n_words(corpus, n=None):
    vec = CountVectorizer(stop_words = 'english').fit(corpus)
    bag_of_words = vec.transform(corpus)
    sum_words = bag_of_words.sum(axis=0) 
    words_freq = [(word, sum_words[0, idx]) for word, idx in vec.vocabulary_.items()]
    words_freq =sorted(words_freq, key = lambda x: x[1], reverse=True)
    return words_freq[:n]
    
common_words = get_top_n_words(df_user_rev['review'], 40)
# for word, freq in common_words:
#     print(word, freq)
df2 = pd.DataFrame(common_words, columns = ['ReviewText' , 'count'])
df2.groupby('ReviewText').sum()['count'].sort_values(ascending=False).iplot(
    kind='bar', yTitle='Count', linecolor='black', title='Top 20 words in review after removing stop words')


### 2-Grams Analysis

In [24]:
def get_top_n_bigram(corpus, n=None):
    vec = CountVectorizer(ngram_range=(2, 2), stop_words='english').fit(corpus)
    bag_of_words = vec.transform(corpus)
    sum_words = bag_of_words.sum(axis=0) 
    words_freq = [(word, sum_words[0, idx]) for word, idx in vec.vocabulary_.items()]
    words_freq =sorted(words_freq, key = lambda x: x[1], reverse=True)
    return words_freq[:n]

common_words = get_top_n_bigram(df_user_rev['review'], 40)

# for word, freq in common_words:
#     print(word, freq)
df4 = pd.DataFrame(common_words, columns = ['ReviewText' , 'count'])
df4.groupby('ReviewText').sum()['count'].sort_values(ascending=False).iplot(
    kind='bar', yTitle='Count', linecolor='black', title='Top 20 bigrams in review after removing stop words')


### 3-Grams Analysis

In [25]:
def get_top_n_trigram(corpus, n=None):
    vec = CountVectorizer(ngram_range=(3, 3), stop_words='english').fit(corpus)
    bag_of_words = vec.transform(corpus)
    sum_words = bag_of_words.sum(axis=0) 
    words_freq = [(word, sum_words[0, idx]) for word, idx in vec.vocabulary_.items()]
    words_freq =sorted(words_freq, key = lambda x: x[1], reverse=True)
    return words_freq[:n]

common_words = get_top_n_trigram(df_user_rev['review'], 20)

# for word, freq in common_words:
#     print(word, freq)
df6 = pd.DataFrame(common_words, columns = ['ReviewText' , 'count'])
df6.groupby('ReviewText').sum()['count'].sort_values(ascending=False).iplot(
    kind='bar', yTitle='Count', linecolor='black', title='Top 20 trigrams in review after removing stop words')

# Game Aesthetics Analysis

## Part-Of-Speech Tagging (POS) Analysis

In [54]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/gio/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [55]:
blob = TextBlob(str(df_user_rev['review']))
pos_df = pd.DataFrame(blob.tags, columns = ['word' , 'pos'])
pos_df = pos_df.pos.value_counts()[:20]
pos_df.iplot(
    kind='bar',
    xTitle='POS',
    yTitle='count', 
    title='Top 20 Part-of-speech tagging for review corpus')

## Text Network Analysis
* visualize many-to-many relationships and their strength
* discover complex structures in the data (such as customers using the same email address to receive specific discounts)

https://towardsdatascience.com/text-network-analysis-generate-beautiful-network-visualisations-a373dbe183ca

### Chord Diagram
https://datavizcatalogue.com/methods/chord_diagram.html

## Gameplay Aesthetics from Game Reviews  
How do players understand, perceive, and talk about gameplay?

1. Extracting all sentences in which the word “gameplay” (and variations such as “gameplays”) appeared.
2. identified the POS of the words and parsed the sentences using a POS tagger and a parser
3. Extract all the adjectives which wereused as a pre-nominal modifier to “gameplay” (e.g. “smooth gameplay”) or as an adjectival complement of “gameplay” (e.g. “gameplay was smooth”)

In [ ]:
# 1 Extracting all sentences in which the word “gameplay” (and variations such as “gameplays”) appeared.


# Join DataFrames